---

# S01E02 : The import system - The import statement

Cyril Desjouy

---

The operation of the `import` statement is very complex. The purpose here is not to study precisely how it works, but only to clarify some important points for the user.

## 1. Module search

When you use the `import` statement, the Python interpreter uses the special function `__import__`.
Writing `import os` is a shortcut to the instruction `os = __import__('os')`! Importing a module is creating a module type object that is simply referenced by an ***identifier*** (a name, a variable).

When executing the `import module` instruction, the Python interpreter looks for if `module` has already been imported. If this is the case, it returns the module it has in cache (see next section). If not, it searches in a location list. This search is done in the following order:

* in the standard library,
* in the current directory (where the script is executed),
* in the `PYTHONPATH` (list of directories),
* in the default directory list (list configured at installation of Python).

If the interpreter does not find the name `module` in any of the locations listed above, it will raise the `ImportError` exception. The list of directories in which the interpreter searches for modules/packages is accessible through `sys.path`:
```python
>> import sys
>> sys.path
```

It is quite possible to add directories to this list:
```python
>> import sys
>> sys.path.append(r'/home/cdesjouy/libs/')
>> import my_module_from_my_libs
```

It is important to note that the modification of `sys.path` **is not permanent**. It extends until the interpreter in which the modification was made completes its execution. To permanently add a directory to the list of directories in which Python searches for modules, you must act on the `PYTHONPATH` environment variable. Under Linux or mac, just add this type of line in your `.bashrc`:

```
export PYTHONPATH=$PYTHONPATH:/home/cdesjouy/libs/
```

>**Note: ***** * Under windows, it seems that the file concerned is `autoexec.bat`. Confer:*
* [stackoverflow - add to the PYTHONPATH in windows](https://stackoverflow.com/questions/3701646/how-to-add-to-the-pythonpath-in-windows-so-it-finds-my-modules-packages)
* [Python.org - windows](https://docs.python.org/3.8/using/windows.html)

## 2. Reload a module

As mentioned in the previous section, the instruction `import module` first looks for if `module` has already been imported. If this is the case, the Python interpreter uses the module it has in cache (in memory) instead of searching for it again. This allows to optimize the execution of codes where the same module could be imported several times. However, it is possible to force a module to reload using the `reload` function provided by the standard `importlib` module:

```python
>> import importlib
>> importlib.reload(module)
```

## 3. Absolute and relative imports

Consider the tree structure in Figure 1.

```
                                 project
                                    │
                                    └── package
                                        │ 
                                        ├── module1.py
                                        │
                                        ├── module2.py
                                        │
                                        └── subpackage
                                                │
                                                └── module3.py
  
                                      Fig. 1: A project
```

Python provides two types of import:

* **The absolute import** specifies the resource to be imported using its full path from the project root folder:

```python
import package.module1
import package.subpackage.module3
```

* **The relative import** specifies the resource to be imported in relation to the current location, i.e. the location where the `import` statement is located:

```python
# instructions in file package/module1.py
from .module2 import something
from .subpackage.module3 import something
```

Relative imports can be difficult to interpret. It is not so obvious where the imported resources are located. In large projects where the directory structure is likely to change, relative imports can become a real headache. In general, absolute imports are preferred because they remain simple and clear and the location of imported resources is explicit. 

## 4. Note on the attribute `__all__`

Consider the tree structure in Figure 1. When the following instruction is executed, one would expect the Python interpreter to import all the modules contained in the package:
```python
>> from package import *
>> dir()
```
This is not the case. The list returned by the `dir` function contains neither `module1` nor `module2`, which means that they have not been imported into our ***namespace***. In fact, when the Python interpreter encounters a global `import` (`*`), it first looks for if the file `__init__.py` (if it exists) contains the special variable `__all__`. This variable can contain a list of resource names (strings). For example:
```python
__all__ = ['module1', 'module2']        ]
```
The interpreter then acts according to:
* if `__all__` is defined, `from package import *` imports the **modules listed** in `__all__`,
* if `__all__` is not defined, `from package import *` imports **nothing**.

The variable `__all__` can also be defined at the module level. In this case:

* if `__all__` is defined, `from module import *` only imports **the objects in this list**,
* if `__all__` is not defined, `from module import *` imports **all objects contained in the module**.

## References

* [Python.org - Modules](https://docs.python.org/3.8/tutorial/modules.html)
* [Python.org - Import](https://docs.python.org/3.8/reference/import.html)
* [Real Python - Modules & Packages](https://realpython.com/python-modules-packages/)
* [Real Python - Absolute vs. relative impors](https://realpython.com/absolute-vs-relative-python-imports/)